This script is an experiment in analyzing multi-hazard impacts on the power grid

The goal of this script is to identify a candidate set of wildfire + space weather events

It uses the following approach:
- Read in set of wildfire events from XXXX
- Get time period, get spatial extent (GIS) -> visualize it
- Highest level: get space weather indices
    - more granular is to get magnetometers and GNSS data (GIMs, likely) in the area of the fire 
- Get HIFLD grid affected based on the wildfire
- (optional) get observed power grid disturbances that overlap in space and time
- Record the candidate event for forensic analysis (social media, interviews, grey literature exploration)


(possibility of a new approach)
- Get wildfire point 
- Choose radius of some sort
- Get any power grid disturbance that occurred within that time and circle
- Inspect space weather data for preceding day to current time
- Store full multi-hazard data for the candidate event and study forensically


TODO
- the connection may very well come from space weather effects on communications during wildfire events (need to incorporate radiation data to represent space weather) 
- 

#### Dependencies and Custom Functions

In [257]:
import numpy as np
import pandas as pd
import os, sys

from datetime import datetime, time
import geopandas as gpd

import matplotlib.pyplot as plt
import matplotlib.dates as mdates
from matplotlib.dates import DateFormatter

from shapely.geometry import Polygon, MultiPolygon

import contextily as ctx


import supermag_api

import re


In [421]:
def get_sm_one_minute(start,end):

    '''

    
    Dependencies
        supermag-api downloadable from https://supermag.jhuapl.edu/mag/?fidelity=low&start=2001-01-01T00%3A00%3A00.000Z&interval=1%3A00%3A00&tab=api
            --> one should move this to the working directory and rename to supermag_api
        datetime
            
    Notes
        it appears this will only work for a few-day request; for longer periods, need to download the data directly
            
    '''


#     import supermag_api
#     import datetime

    start_datetime = pd.to_datetime(start)
    end_datetime = pd.to_datetime(end)
    
    # get the number of days between start and end
    num_days = (end_datetime - start_datetime).days
    print('the number of days that will be requested is {}'.format(num_days))
    input('Press Enter if you are sure you want to ping the SuperMAG API for this...')
    
    # get correct format for 'start date'
    date_obj_start = datetime.strptime(start, '%Y-%m-%d %H:%M:%S')
    formatted_start = date_obj_start.strftime('%Y-%m-%dT%H:%M')

    (status,df_smidxs) = supermag_api.SuperMAGGetIndices('rymc1012',formatted_start,86400*num_days,'SME, SMU, SML, SMR')

    datetimes_sm = [pd.to_datetime(t, unit='s') for t in df_smidxs['tval']]

    df_smidxs['datetimes'] = datetimes_sm
    df_smidxs = df_smidxs.set_index(['datetimes'])
    df_smidxs.index = pd.to_datetime(df_smidxs.index)
    
    return df_smidxs





#### Wildfire database

Some things I'm learning about wildfire data
- MODIS might be best available given coverage
- There is a NASA digital twin project https://ideas-digitaltwin.jpl.nasa.gov/airquality/, but it is focused on air quality and thus the atmospheric emissions associated with wildfire, whereas for this work I need the wildfires themselves (note their emissions which then mix with the atmosphere and its dynamics)
- ...


In [2]:
# NASA FIRMS data https://firms.modaps.eosdis.nasa.gov


# National Interagency Fire Center https://www.nifc.gov/
file_path_nifc_wildfire = "/Users/ryanmc/Documents/Conferences/Jack_Eddy_Symposium_2022/dev/wildfire_data/WFIGS_Incident_Locations_6818922478522849878.geojson"
file_path_modis_wildfire = "/Users/ryanmc/Documents/Conferences/Jack_Eddy_Symposium_2022/dev/wildfire_data/DL_FIRE_M-C61_530609/fire_archive_M-C61_530609.shp"
# file_path_suomi_wildfire = "/Users/ryanmc/Documents/Conferences/Jack_Eddy_Symposium_2022/dev/wildfire_data/DL_FIRE_SV-C2_530613/fire_archive_SV-C2_530613.shp"

# gdf_nifc_wildfire = gpd.read_file(file_path_nifc_wildfire)
gdf_modis_wildfire = gpd.read_file(file_path_modis_wildfire)
# gdf_suomi_wildfire = gpd.read_file(file_path_suomi_wildfire)




In [3]:
# Explore the first few rows
print(gdf_modis_wildfire.head())

# Check the geometry type (e.g., Point, Polygon, LineString)
print(gdf_modis_wildfire.geom_type.unique())

# Get summary of the attributes
print(gdf_modis_wildfire.info())

# # Plot the shapefile (quick visualization)
# gdf.plot()


   LATITUDE  LONGITUDE  BRIGHTNESS  SCAN  TRACK    ACQ_DATE ACQ_TIME  \
0   26.5690   -81.0586       328.5   2.5    1.5  2023-01-01     1819   
1   26.5640   -81.0828       327.4   2.5    1.5  2023-01-01     1819   
2   26.5611   -81.0496       318.6   2.5    1.5  2023-01-01     1819   
3   26.5507   -81.0793       310.5   2.5    1.5  2023-01-01     1819   
4   26.5557   -81.0552       310.1   2.5    1.5  2023-01-01     1819   

  SATELLITE INSTRUMENT  CONFIDENCE VERSION  BRIGHT_T31   FRP DAYNIGHT  TYPE  \
0      Aqua      MODIS          83   61.03       294.2  81.2        D     0   
1      Aqua      MODIS          82   61.03       294.4  76.7        D     0   
2      Aqua      MODIS          73   61.03       294.6  41.4        D     0   
3      Aqua      MODIS          57   61.03       293.5  17.9        D     0   
4      Aqua      MODIS          54   61.03       294.9  17.2        D     0   

                     geometry  
0  POINT (-81.05860 26.56900)  
1  POINT (-81.08280 26.56400

In [7]:
# Explore the first few rows
print(gdf_suomi_wildfire.head())

# Check the geometry type (e.g., Point, Polygon, LineString)
print(gdf_suomi_wildfire.geom_type.unique())

# Get summary of the attributes
print(gdf_suomi_wildfire.info())

# # Plot the shapefile (quick visualization)
# gdf.plot()


   LATITUDE  LONGITUDE  BRIGHTNESS  SCAN  TRACK    ACQ_DATE ACQ_TIME  \
0  40.63593  -74.22243      304.95  0.44   0.38  2023-01-01     0639   
1  40.63527  -74.21728      300.21  0.44   0.38  2023-01-01     0639   
2  39.96399  -76.59748      299.41  0.53   0.42  2023-01-01     0640   
3  38.73565  -77.66982      313.24  0.38   0.43  2023-01-01     0640   
4  37.41987  -77.43283      327.20  0.54   0.42  2023-01-01     0640   

  SATELLITE INSTRUMENT CONFIDENCE VERSION  BRIGHT_T31   FRP DAYNIGHT  TYPE  \
0         N      VIIRS          n       2      284.65  1.89        N     0   
1         N      VIIRS          n       2      282.67  1.41        N     0   
2         N      VIIRS          n       2      279.76  1.05        N     0   
3         N      VIIRS          n       2      281.92  1.38        N     0   
4         N      VIIRS          n       2      283.63  3.07        N     0   

                     geometry  
0  POINT (-74.22243 40.63593)  
1  POINT (-74.21728 40.63527)  
2 

In [367]:
if 'ACQ_DATE' in gdf_modis_wildfire.columns and 'ACQ_TIME' in gdf_modis_wildfire.columns:
    gdf_modis_wildfire['datetime'] = (
        gdf_modis_wildfire['ACQ_DATE'].astype(str) + ' ' + gdf_modis_wildfire['ACQ_TIME'].astype(str)
    )
    gdf_modis_wildfire['datetime'] = pd.to_datetime(gdf_modis_wildfire['datetime'])
else:
    raise ValueError("Expected 'ACQ_DATE' and 'ACQ_TIME' columns.")

In [ ]:
# Group by unique acquisition dates and times
unique_datetimes = gdf_modis_wildfire['datetime'].unique()

# Loop over each unique datetime and plot the corresponding points
for dt in unique_datetimes:
    subset = gdf_modis_wildfire[gdf_modis_wildfire['datetime'] == dt]

    # Plot the points for this specific acquisition time
    fig, ax = plt.subplots(figsize=(10, 6))
    subset.plot(ax=ax, color='red', marker='o', markersize=5)

    # Customize plot title and labels
    ax.set_title(f"Acquisition Date and Time: {dt}", fontsize=15)
    ax.set_xlabel("Longitude")
    ax.set_ylabel("Latitude")
    
#     ax = subset.to_crs(epsg=3857).plot(ax=ax, color='red', marker='o', markersize=5)
    ctx.add_basemap(ax)
    
    # Display the plot
    plt.show()
    
    input('push any button...')

In [ ]:
import folium
from folium.plugins import TimestampedGeoJson



# Convert GeoDataFrame to GeoJSON-like dictionary with timestamp for Folium
features = []
for _, row in gdf_modis_wildfire.iterrows():
    feature = {
        'type': 'Feature',
        'geometry': row['geometry'].__geo_interface__,
        'properties': {
            'time': row['datetime'].isoformat(),  # Use ISO format for timestamps
            'popup': f"Acquired: {row['datetime']}"
        }
    }
    features.append(feature)

# Create the Timestamped GeoJSON layer
timestamped_geojson = TimestampedGeoJson(
    {'type': 'FeatureCollection', 'features': features},
    period='PT1H',  # Period for animation: 1 hour
    add_last_point=False,
    auto_play=False,
    loop=True,
    max_speed=1,
    loop_button=True,
    date_options='YYYY-MM-DD HH:mm:ss',
    time_slider_drag_update=True
)

# Initialize a Folium map centered on the dataset's centroid
m = folium.Map(
    location=[gdf_modis_wildfire.geometry.y.mean(), gdf_modis_wildfire.geometry.x.mean()],
    zoom_start=6, tiles='CartoDB positron'
)

# Add the timestamped layer to the map
timestamped_geojson.add_to(m)

# Save the map as an HTML file and display it
m.save('interactive_map.html')

# If running in Jupyter, display the map directly
m


In [ ]:
# Create a list of features grouped by unique timestamps
features = []
for dt, group in gdf_modis_wildfire.groupby('datetime'):
    feature = {
        'type': 'FeatureCollection',
        'features': [
            {
                'type': 'Feature',
                'geometry': row['geometry'].__geo_interface__,
                'properties': {
                    'time': dt.isoformat(),  # Set timestamp in ISO format
                    'popup': f"Acquired: {dt}"
                }
            }
            for _, row in group.iterrows()
        ]
    }
    features.append(feature)


# Create the TimestampedGeoJson with these features
timestamped_geojson = TimestampedGeoJson(
    {'type': 'FeatureCollection', 'features': features},
    period='PT1H',              # Set period of time for each step (1 hour)
    add_last_point=False,        # Ensure only current points appear
    auto_play=False,              # Automatically start animation
    loop=True,                   # Loop the animation
    max_speed=1,                 # Normal animation speed
    loop_button=True,            # Allow user to loop animation
    date_options='YYYY-MM-DD HH:mm:ss',  # Display format for timestamps
    time_slider_drag_update=True # Update on dragging time slider
)

# Initialize the Folium map centered on the dataset's centroid
m = folium.Map(
    location=[gdf_modis_wildfire.geometry.y.mean(), gdf_modis_wildfire.geometry.x.mean()],
    zoom_start=6, 
    tiles='CartoDB positron'  # Light basemap
)

# Add the timestamped GeoJSON to the map
timestamped_geojson.add_to(m)

# Save the map as an HTML file and display it
m.save('interactive_map.html')

# If running in Jupyter, display the map directly
m

#### HIFLD data
uses HIFLD data: https://hifld-geoplatform.hub.arcgis.com/datasets/geoplatform::transmission-lines

In [ ]:
file_path_powergrid = "/Users/ryanmc/Documents/Conferences/Jack_Eddy_Symposium_2022/dev/physical_grid_data/U.S._Electric_Power_Transmission_Lines.geojson"
gdf_powergrid = gpd.read_file(file_path_powergrid)



#### Power Grid Disturbance Data

Candidates
- [new dataset from EAGLE-I](https://www.nature.com/articles/s41597-024-03095-5) (Data are available in the Figshare repository at https://doi.org/10.6084/m9.figshare.24237376) 
- [DOE electric disturbance events OE-417](https://www.oe.netl.doe.gov/OE417_annual_summary.aspx)


In [18]:
# Read in 2023 data
outage_directory = '/Users/ryanmc/Documents/Conferences/Jack_Eddy_Symposium_2022/dev/outage_data/'
oe417 = pd.read_excel(os.path.join(outage_directory,'DOE-OE-417/2023_Annual_Summary.xlsx'),header=1)
oe417 = oe417.dropna(subset=['Time Event Began'])
oe417 = oe417.iloc[:-2]
for o in range(len(oe417['Number of Customers Affected'])):
    if oe417['Number of Customers Affected'].iloc[o]=='Unknown':
        oe417['Number of Customers Affected'].iloc[o] = np.nan
    elif type(oe417['Number of Customers Affected'].iloc[o]) == str: 
        oe417['Number of Customers Affected'].iloc[o] = int(oe417['Number of Customers Affected'].iloc[o])
    
oe417 = oe417[oe417['Number of Customers Affected']>1000]

eaglei = pd.read_csv(os.path.join(outage_directory,'EAGLE-I/eaglei_outages_2023.csv'))
eaglei = eaglei[eaglei['customers_out']>1000]


In [34]:
oe417

Event Month     Date Event Began Time Event Began  Date of Restoration  \
2       January           01/01/2023         14:47:00           01/01/2023   
5       January           01/02/2023         18:22:00           01/02/2023   
7       January           01/05/2023         08:19:00           01/05/2023   
10      January           01/07/2023         22:00:00           01/08/2023   
11      January           01/07/2023         23:44:00           01/08/2023   
..          ...                  ...              ...                  ...   
336    December  2023-12-18 00:00:00         05:45:00            - Unknown   
338    December  2023-12-19 00:00:00         00:41:00  2023-12-19 00:00:00   
340    December  2023-12-23 00:00:00         00:43:00  2023-12-23 00:00:00   
342    December  2023-12-25 00:00:00         19:56:00  2023-12-25 00:00:00   
344    December  2023-12-27 00:00:00         14:44:00  2023-12-28 00:00:00   

    Time of Restoration                                      Area Affected  \
2              16:50:00                            Florida: Citrus County;   
5              22:27:00  Arkansas: Union County; Louisiana: Ouachita Pa...   
7              08:20:00                       Louisiana: Concordia Parish;   
10             21:00:00                     California: Sacramento County;   
11             02:29:00                Texas: Jasper County, Tyler County;   
..                  ...                                                ...   
336           - Unknown                                    ISO New England   
338            00:47:00                                        LUMA Energy   
340            00:48:00                                        LUMA Energy   
342            20:01:00                                        LUMA Energy   
344            04:14:00                                Otter Tail Power Co   

    NERC Region                                     Alert Criteria  \
2          SERC  Physical attack that could potentially impact ...   
5          SERC  Unexpected Transmission loss within its area, ...   
7          SERC  Electrical System Separation (Islanding) where...   
10         WECC  Loss of electric service to more than 50,000 c...   
11          TRE  Unexpected Transmission loss within its area, ...   
..          ...                                                ...   
336        WECC  Loss of electric service to more than 50,000 c...   
338         NaN  Firm load shedding of 100 Megawatts or more im...   
340         NaN  Firm load shedding of 100 Megawatts or more im...   
342         NaN  Firm load shedding of 100 Megawatts or more im...   
344         MRO  Electrical System Separation (Islanding) where...   

                        Event Type Demand Loss (MW)  \
2                        Vandalism               19   
5                   Severe Weather               20   
7        Transmission Interruption               23   
10                  Severe Weather              458   
11       Transmission Interruption               20   
..                             ...              ...   
336  - Weather or natural disaster          Unknown   
338    - Generator loss or failure               77   
340    - Generator loss or failure               65   
342    - Generator loss or failure              105   
344  - Weather or natural disaster               14   

    Number of Customers Affected  
2                           3509  
5                           6849  
7                           1631  
10                        185434  
11                          9823  
..                           ...  
336                       730000  
338                        50204  
340                        37850  
342                        36100  
344                         8000  

[85 rows x 11 columns]

In [352]:

def get_datetime_oe417(str_date,dt_time):
    date_obj = datetime.strptime(str_date, '%m/%d/%Y')
    dt = datetime.combine(date_obj, dt_time)

    return dt

# Regular expression to capture 'State: County' pairs
pattern = r'(\w+):\s*([\w\s-]+)'

# Function to extract states and counties from each row
# def extract_state_county_pairs(row):
#     pairs = []
#     # Split by semicolon to handle multiple state-county pairs
#     entries = row.split(';')
#     for entry in entries:
#         # Use regex to extract state and county
#         match = re.match(r'(\w+):\s*(.*)', entry.strip())
#         if match:
#             state = match.group(1)
#             county = match.group(2)
#             pairs.append((state, county))
#     return pairs

def extract_state_county_pairs(location_str):
    pairs = []

    # Split by ';' to handle multiple state-county blocks
    state_county_blocks = location_str.split(';')

    for block in state_county_blocks:
        block = block.strip()

        # Case: Handle multiple consecutive states without counties (e.g., "Alabama: Maine:")
        if re.fullmatch(r"(.+?:)+", block):
            states = [state.strip() for state in block.split(':') if state.strip()]
            for state in states:
                pairs.append((state, None))  # Store each state with None for county
            continue  # Skip further processing for this block

        # Use regex to match "State: County, County, ..." or "State:"
        match = re.match(r"(.+?):\s*(.*)", block)

        if match:
            state = match.group(1).strip()
            counties = match.group(2).strip()

            if counties:  # If counties exist, split them by ','
                counties_list = [county.strip() for county in counties.split(',')]
                for county in counties_list:
                    pairs.append((state, county))
            else:  # If no counties are provided
                pairs.append((state, None))
        else:
            # If the block contains only a state name
            pairs.append((block, None))

    return pairs


def get_oe417_geometries(row_area_affected,gdf_states,gdf_counties):
    '''
        inputs: 
            - row of oe417 data for Area Affected (oe417['Area Affected'].iloc[x])
            - data for states geometries
            - data for county geometries
        dependencies:
            - extract_state_county_pairs function
    '''
    
    row_states_counties = extract_state_county_pairs(row_area_affected)
    all_geometries = []
    for l in row_states_counties: 
        if not l[0]:
            # skip the empty rows in the extracted data
            continue
        else:
            if not l[1]:
                # if there is no county data, then just use whole state
                geom_data_tmp = gpd.GeoSeries(gdf_states['geometry'][gdf_states['NAME'] == l[0]].values)
                if geom_data_tmp.empty:
                    continue
                if geom_data_tmp.apply(lambda geom: isinstance(geom, MultiPolygon)).all():
#                     print('----> encountering multipolygon for {}, skipping'.format(l[0]))
                    all_geometries.extend([polygon for polygon in geom_data_tmp.geometry[0].geoms])
                else:
                    all_geometries.extend( [Polygon(geom_data_tmp.geometry[0])] )
            else:
                # if there is county data, get the county geometries and combine them
                fips_tmp = get_fips(l[0])
                geom_data_tmp = gpd.GeoSeries(gdf_counties['geometry'][ (gdf_counties['STATEFP'] == fips_tmp) & (gdf_counties['NAMELSAD'] == l[1]) ].values)
                if geom_data_tmp.empty:
                    continue
                if geom_data_tmp.apply(lambda geom: isinstance(geom, MultiPolygon)).all():
#                     print('----> encountering multipolygon for {}, skipping'.format(l[0]))
                    all_geometries.extend([polygon for polygon in geom_data_tmp.geometry[0].geoms])
                else:
                    all_geometries.extend( [Polygon(geom_data_tmp.geometry[0])] )

    combined_geometry = gpd.GeoSeries(all_geometries).unary_union

    return combined_geometry, row_states_counties

def get_eaglei_geometries(row_county,row_state,gdf_states,gdf_counties):
    '''
        inputs: 
            - row of eaglei data for county (eagelei['county'].iloc[x])
            - row of eaglei data for state (eagelei['state'].iloc[x])
            - data for states geometries
            - data for county geometries
        dependencies:
            - extract_state_county_pairs function
    '''
    
    all_geometries = []
    fips_tmp = get_fips(row_state)
    geom_data_tmp = gpd.GeoSeries(gdf_counties['geometry'][ (gdf_counties['STATEFP'] == fips_tmp) & (gdf_counties['NAMELSAD'] == row_county + ' County') ].values)
    if geom_data_tmp.empty:
        return np.nan
    if geom_data_tmp.apply(lambda geom: isinstance(geom, MultiPolygon)).all():
        all_geometries.extend([polygon for polygon in geom_data_tmp.geometry[0].geoms])
    else:
        all_geometries.extend( [Polygon(geom_data_tmp.geometry[0])] )
    

    combined_geometry = gpd.GeoSeries(all_geometries).unary_union

    return combined_geometry

# Dictionary mapping state abbreviations to FIPS codes
# List of tuples containing (state_abbreviation, fips_code, full_state_name)
state_fips = [
    ('AL', '01', 'Alabama'),
    ('AK', '02', 'Alaska'),
    ('AZ', '04', 'Arizona'),
    ('AR', '05', 'Arkansas'),
    ('CA', '06', 'California'),
    ('CO', '08', 'Colorado'),
    ('CT', '09', 'Connecticut'),
    ('DE', '10', 'Delaware'),
    ('FL', '12', 'Florida'),
    ('GA', '13', 'Georgia'),
    ('HI', '15', 'Hawaii'),
    ('ID', '16', 'Idaho'),
    ('IL', '17', 'Illinois'),
    ('IN', '18', 'Indiana'),
    ('IA', '19', 'Iowa'),
    ('KS', '20', 'Kansas'),
    ('KY', '21', 'Kentucky'),
    ('LA', '22', 'Louisiana'),
    ('ME', '23', 'Maine'),
    ('MD', '24', 'Maryland'),
    ('MA', '25', 'Massachusetts'),
    ('MI', '26', 'Michigan'),
    ('MN', '27', 'Minnesota'),
    ('MS', '28', 'Mississippi'),
    ('MO', '29', 'Missouri'),
    ('MT', '30', 'Montana'),
    ('NE', '31', 'Nebraska'),
    ('NV', '32', 'Nevada'),
    ('NH', '33', 'New Hampshire'),
    ('NJ', '34', 'New Jersey'),
    ('NM', '35', 'New Mexico'),
    ('NY', '36', 'New York'),
    ('NC', '37', 'North Carolina'),
    ('ND', '38', 'North Dakota'),
    ('OH', '39', 'Ohio'),
    ('OK', '40', 'Oklahoma'),
    ('OR', '41', 'Oregon'),
    ('PA', '42', 'Pennsylvania'),
    ('RI', '44', 'Rhode Island'),
    ('SC', '45', 'South Carolina'),
    ('SD', '46', 'South Dakota'),
    ('TN', '47', 'Tennessee'),
    ('TX', '48', 'Texas'),
    ('UT', '49', 'Utah'),
    ('VT', '50', 'Vermont'),
    ('VA', '51', 'Virginia'),
    ('WA', '53', 'Washington'),
    ('WV', '54', 'West Virginia'),
    ('WI', '55', 'Wisconsin'),
    ('WY', '56', 'Wyoming'),
]

def get_fips(state_name):
    for abbr, fips, name in state_fips:
        if name.upper() == state_name.upper():
            return fips
    return None, None  # Return None if not found

##### Country/State location data
Geting the data from [US Census Bureau Tiger platform](https://www.census.gov/geographies/mapping-files/time-series/geo/tiger-line-file.html)

In [ ]:
gdf_states = gpd.read_file('/Users/ryanmc/Documents/Conferences/Jack_Eddy_Symposium_2022/dev/location_data/Census_Bureau_Data/tl_2023_us_state/tl_2023_us_state.shp')
gdf_counties = gpd.read_file('/Users/ryanmc/Documents/Conferences/Jack_Eddy_Symposium_2022/dev/location_data/Census_Bureau_Data/tl_2023_us_county/tl_2023_us_county.shp')

In [353]:
# Merge into one outage data file as a gpd
outage_columns = ['outage_start_time', 'outage_stop_time', 'customers_affected','geometry','source']
outage_data_gdf = gpd.GeoDataFrame(pd.DataFrame(columns=outage_columns), geometry='geometry')

outage_data_gdf.set_crs("EPSG:4326", inplace=True)  # WGS84 - lat/lon

for o in range(len(oe417)):
    
    # get start and end times
    str_date_start = oe417['Date Event Began'].iloc[o]
    dt_time_start = oe417['Time Event Began'].iloc[o]
    str_date_end = oe417['Date of Restoration'].iloc[o]
    dt_time_end = oe417['Time of Restoration'].iloc[o]
    try:
        dt_start = get_datetime_oe417(str_date_start,dt_time_start)
    except:
        dt_start = np.nan
    try:
        dt_end = get_datetime_oe417(str_date_end,dt_time_end)
    except:
        dt_end = np.nan    
    
    # get the geometries of the areas affected
    combined_geometry, states_counties = get_oe417_geometries(oe417['Area Affected'].iloc[o],gdf_states,gdf_counties)
    
    
    outage_data_gdf = outage_data_gdf.append({
                                            'source': 'oe417', 
                                            'area affected': states_counties, 
                                            'outage_start_time': dt_start,
                                            'outage_stop_time': dt_end,
                                            'customers_affected': oe417['Number of Customers Affected'].iloc[o],
                                            'geometry': combined_geometry
                                                }, ignore_index=True)

    
for e in range(len(eaglei)):
    
    # get start times
    try:
        dt_start = pd.to_datetime(eaglei['run_start_time'].iloc[0], format='%m/%d/%y %H:%M')
    except:
        dt_start = np.nan
    
    combined_geometry = get_eaglei_geometries(eaglei['county'].iloc[e],eaglei['state'].iloc[e],gdf_states,gdf_counties)
    
    outage_data_gdf = outage_data_gdf.append({
                                                'source': 'eaglei', 
                                                'area affected': [(eaglei['state'].iloc[e],eaglei['county'].iloc[e]+' County')], 
                                                'outage_start_time': dt_start,
                                                'outage_stop_time': np.nan,
                                                'customers_affected': eaglei['customers_out'].iloc[e],
                                                'geometry': combined_geometry
                                                    }, ignore_index=True)

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:27: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

...

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  outage_data_gdf = outage_data_gdf.append({
/var/folders/56/vhtxcmr565z5ksdt3g3px27w0000gq/T/ipykernel_55220/1970426275.py:47: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
 

In [355]:
outage_data_gdf

outage_start_time    outage_stop_time customers_affected  \
0     2023-01-01 14:47:00 2023-01-01 16:50:00               3509   
1     2023-01-02 18:22:00 2023-01-02 22:27:00               6849   
2     2023-01-05 08:19:00 2023-01-05 08:20:00               1631   
3     2023-01-07 22:00:00 2023-01-08 21:00:00             185434   
4     2023-01-07 23:44:00 2023-01-08 02:29:00               9823   
...                   ...                 ...                ...   
29843 2023-01-01 00:00:00                 NaT               3245   
29844 2023-01-01 00:00:00                 NaT               1503   
29845 2023-01-01 00:00:00                 NaT               1007   
29846 2023-01-01 00:00:00                 NaT               3596   
29847 2023-01-01 00:00:00                 NaT               1373   

                                                geometry  source  \
0      POLYGON ((-83.18791 28.98657, -82.99976 28.989...   oe417   
1      MULTIPOLYGON (((-91.93628 32.65886, -91.93574 ...   oe417   
2      POLYGON ((-91.51807 31.52815, -91.51818 31.527...   oe417   
3      POLYGON ((-121.43991 38.25553, -121.44002 38.2...   oe417   
4      POLYGON ((-94.45780 31.03333, -94.45746 31.033...   oe417   
...                                                  ...     ...   
29843  POLYGON ((-73.50846 42.49373, -73.50953 42.493...  eaglei   
29844  POLYGON ((-96.00135 36.34750, -96.00133 36.349...  eaglei   
29845  POLYGON ((-78.20651 41.88498, -78.20652 41.884...  eaglei   
29846  POLYGON ((-109.10668 39.46221, -109.10649 39.4...  eaglei   
29847  POLYGON ((-111.73757 40.52820, -111.73771 40.5...  eaglei   

                                           area affected  
0                   [(Florida, Citrus County), (, None)]  
1      [(Arkansas, Union County), (Louisiana, Ouachit...  
2              [(Louisiana, Concordia Parish), (, None)]  
3            [(California, Sacramento County), (, None)]  
4      [(Texas, Jasper County), (Texas, Tyler County)...  
...                                                  ...  
29843                    [(New York, Rensselaer County)]  
29844                         [(Oklahoma, Tulsa County)]  
29845                    [(Pennsylvania, McKean County)]  
29846                             [(Utah, Grand County)]  
29847                         [(Utah, Salt Lake County)]  

[29848 rows x 6 columns]

PICK UP HERE WITH....

    - check the issue with datetimes in the 2023 eaglei data (how to get the actual times of outages, not 'collection run time'
    - need to aggregate close wildfire points into single 'event'

#### Candidate search


In [422]:
candidate_columns = ['outage_start_time', 'outage_stop_time', 'customers_affected','geometry','source']
candidate_gdf = gpd.GeoDataFrame(pd.DataFrame(columns=outage_columns), geometry='geometry')


for w in range(len(gdf_modis_wildfire)):
    
    # Identify overlap in time with the power grid disturbance
    wildfire_datetime = gdf_modis_wildfire['datetime'].iloc[w]
    filtered_outage_data_gdf = outage_data_gdf[
                                            (outage_data_gdf['outage_start_time'] >= wildfire_datetime - pd.Timedelta(hours=1)) &
                                            (outage_data_gdf['outage_start_time'] <= wildfire_datetime + pd.Timedelta(days=1))
                                            ]
    
    # Identify overlap in space with the power grid disturbance
    #   Create a buffer (circular area) around the point
    radius = 0.1  # Example radius in degrees (adjust based on your CRS)
    wildfire_point = gdf_modis_wildfire['geometry'].iloc[w]
    buffered_wildfire_point = wildfire_point.buffer(radius)
    for f in range(len(filtered_outage_data_gdf)):
        if buffered_wildfire_point.intersects(filtered_outage_data_gdf['geometry'].iloc[f]):
            
            # Check space weather data for space weather conditions (if at any time in the surrounding 24 hours AE exceeded 200 nT)
            sm_data = get_sm_one_minute((wildfire_datetime - pd.Timedelta(hours=24)).strftime('%Y-%-m-%-d %H:%M:%S'),
                                        (wildfire_datetime + pd.Timedelta(hours=12)).strftime('%Y-%-m-%-d %H:%M:%S'))
            
            if sm_data['SME'][sm_data['SME']>200.].any():

                # save as a candidate
                print('candidate at {}! \n wildfire: \n \t {},{} \n outage: \n \t {} for {} \n sp wx: \n \t {} at {}'.format(gdf_modis_wildfire['datetime'].iloc[w],
                                                                                                                             gdf_modis_wildfire['LATITUDE'].iloc[w],
                                                                                                                             gdf_modis_wildfire['LONGITUDE'].iloc[w],
                                                                                                                             filtered_outage_data_gdf['outage_start_time'].iloc[f],
                                                                                                                             filtered_outage_data_gdf['area affected'].iloc[f],
                                                                                                                             sm_data['SME'][sm_data['SME']==sm_data['SME'].max()].values,
                                                                                                                             sm_data.index[sm_data['SME']==sm_data['SME'].max()].values,))
            
            


the number of days that will be requested is 1
Press Enter if you are sure you want to ping the SuperMAG API for this...
candidate at 2023-01-11 15:41:00! 
 wildfire: 
 	 32.9785,-82.4681 
 outage: 
 	 2023-01-12 14:00:00 for [('Alabama', None), ('Georgia', None)] 
 sp wx: 
 	 [503.498718] at ['2023-01-10T22:48:00.000000000']
the number of days that will be requested is 1
Press Enter if you are sure you want to ping the SuperMAG API for this...
candidate at 2023-01-11 15:41:00! 
 wildfire: 
 	 32.9768,-82.4518 
 outage: 
 	 2023-01-12 14:00:00 for [('Alabama', None), ('Georgia', None)] 
 sp wx: 
 	 [503.498718] at ['2023-01-10T22:48:00.000000000']
the number of days that will be requested is 1
Press Enter if you are sure you want to ping the SuperMAG API for this...
candidate at 2023-01-11 15:41:00! 
 wildfire: 
 	 32.6894,-82.4514 
 outage: 
 	 2023-01-12 14:00:00 for [('Alabama', None), ('Georgia', None)] 
 sp wx: 
 	 [503.498718] at ['2023-01-10T22:48:00.000000000']
the number of da

KeyboardInterrupt: Interrupted by user